In [1]:
# ================================================================
# UFO MERGE PIPELINE V2 — JSONL ONLY
# FULL PROVENANCE + SOURCE ROW NUMBERS + TOP-LEVEL METADATA HEADER
# ================================================================
import os, json, hashlib
import pandas as pd
import numpy as np

ROOT = "/content"
MERGE_VERSION = "ufo_v2_2025_01_28"

# ---------------------------------------------------------------
# FIND CSV FILES
# ---------------------------------------------------------------
csv_paths = [
    os.path.join(ROOT, f)
    for f in os.listdir(ROOT)
    if f.lower().endswith(".csv")
]

print("FOUND CSV FILES:", len(csv_paths))

# ---------------------------------------------------------------
# BULLETPROOF CSV LOADER
# ---------------------------------------------------------------
def load_csv(fp):
    with open(fp, "r", encoding="utf-8", errors="ignore") as f:
        s = f.read(4096)

    comma = s.count(",")
    tab   = s.count("\t")
    pipe  = s.count("|")

    sep = "," if comma >= tab and comma >= pipe else ("\t" if tab >= pipe else "|")

    df = pd.read_csv(fp, dtype=str, sep=sep, engine="python", on_bad_lines="skip")
    df = df.loc[:, ~df.columns.duplicated()].copy()

    df["source_row_nr"] = df.index
    df["source_file"]   = os.path.basename(fp)

    df["raw_snapshot"] = df.astype(str).agg("|".join, axis=1)
    df["raw_hash"]     = df["raw_snapshot"].apply(lambda x: hashlib.sha1(x.encode()).hexdigest())

    return df

# ---------------------------------------------------------------
# LOAD ALL
# ---------------------------------------------------------------
dfs = [load_csv(fp) for fp in csv_paths]
raw_merged = pd.concat(dfs, ignore_index=True)
print("RAW MERGED:", len(raw_merged))

# ---------------------------------------------------------------
# NORMALIZE
# ---------------------------------------------------------------
df = raw_merged.copy()
df.columns = [c.lower().strip() for c in df.columns]
df = df.loc[:, ~df.columns.duplicated()]

def pick(*names):
    for n in names:
        if n in df.columns:
            return df[n].astype(str)
    return pd.Series([None]*len(df))

df["date_time"] = pick("datetime","date_time","dateoccurred","reported","occurred","sighted_at")
df["city"]      = pick("city","location_city","location.city")
df["state"]     = pick("state","location_state","location.state","province")
df["country"]   = pick("country","location_country","location.country")
df["shape"]     = pick("shape","ufo_shape","form")
df["summary"]   = pick("summary","description","desc","text","comments")

df["duration_seconds"] = pd.to_numeric(
    pick("duration","duration_seconds","encounter_length").str.replace(",", ""),
    errors="coerce"
)

df["latitude"]  = pd.to_numeric(pick("latitude","lat","city_latitude"), errors="coerce")
df["longitude"] = pd.to_numeric(pick("longitude","lon","lng","city_longitude"), errors="coerce")

df["full_text"] = df["summary"].astype(str)

# ---------------------------------------------------------------
# FIXED YEAR PARSING — VECTORIZED + COERCE
# ---------------------------------------------------------------
df["year"] = (
    pd.to_datetime(df["date_time"], errors="coerce")
    .dt.year
    .fillna(-1)
    .astype(int)
)

df["year_context_available"] = df["year"].apply(lambda y: y >= 0)

# ---------------------------------------------------------------
# UUID
# ---------------------------------------------------------------
def make_uuid(row):
    base = (
        str(row["city"]) + "|" +
        str(row["state"]) + "|" +
        str(row["date_time"]) + "|" +
        str(row["shape"]) + "|" +
        str(row["summary"])
    )
    return hashlib.md5(base.encode()).hexdigest()

df["ufo_uuid"] = df.apply(make_uuid, axis=1)

# ---------------------------------------------------------------
# DEDUPE V2 — VECTOR BASED + FULL LINEAGE
# ---------------------------------------------------------------
df["text_hash"] = df["full_text"].str.lower().apply(lambda x: hashlib.md5(x.encode()).hexdigest())
df["duration_bucket"] = (df["duration_seconds"] // 10).fillna(-1).astype(int)

group_cols = ["city","state","date_time","shape","duration_bucket","text_hash"]

agg = {
    "raw_snapshot": list,
    "raw_hash": list,
    "source_file": list,
    "source_row_nr": list,
    "summary": "first",
    "full_text": "first",
    "duration_seconds": "first",
    "latitude": "first",
    "longitude": "first",
    "country": "first",
    "year": "first",
    "year_context_available": "first",
    "ufo_uuid": "first",
}

deduped = df.groupby(group_cols, as_index=False).agg(agg)
print("DEDUPED ROWS:", len(deduped))

# ---------------------------------------------------------------
# BUILD LINEAGE
# ---------------------------------------------------------------
def build_lineage(row):
    return [
        {
            "file": f,
            "row": int(rn),
            "raw_hash": h
        }
        for f, rn, h in zip(
            row["source_file"],
            row["source_row_nr"],
            row["raw_hash"]
        )
    ]

deduped["lineage"] = deduped.apply(build_lineage, axis=1)
deduped = deduped.drop(columns=["source_file","source_row_nr"])

# ---------------------------------------------------------------
# METADATA
# ---------------------------------------------------------------
deduped["merge_version"] = MERGE_VERSION
deduped["dedupe_method"] = "vectorized_signature_v2"

# ---------------------------------------------------------------
# SAVE JSONL
# ---------------------------------------------------------------
raw_out    = "/content/ufo_raw_v2.jsonl"
dedupe_out = "/content/ufo_deduped_v2.jsonl"

df.to_json(raw_out, orient="records", lines=True, force_ascii=False)

with open(dedupe_out, "w", encoding="utf-8") as f:
    header = {
        "dataset": "UFO Witness Corpus v2",
        "merge_version": MERGE_VERSION,
        "generated_at": pd.Timestamp("now").isoformat(),
        "sources": sorted([os.path.basename(p) for p in csv_paths]),
        "dedupe_method": "vectorized_signature_v2",
        "uuid_method": "md5(city|state|datetime|shape|summary)",
        "provenance_fields": ["raw_snapshot","raw_hash","lineage"]
    }
    f.write(json.dumps(header, ensure_ascii=False) + "\n")
    deduped.to_json(f, orient="records", lines=True, force_ascii=False)

print("\nDONE.")
print("RAW JSONL:     ", raw_out)
print("DEDUPED JSONL: ", dedupe_out)


FOUND CSV FILES: 6
RAW MERGED: 486384
DEDUPED ROWS: 242842

DONE.
RAW JSONL:      /content/ufo_raw_v2.jsonl
DEDUPED JSONL:  /content/ufo_deduped_v2.jsonl


In [2]:
# ================================================================
# SECTION 1 — DOWNLOAD ALL REFERENCE DATA NEEDED FOR ENRICHMENT
# ================================================================
import os, requests, hashlib
import pandas as pd

os.makedirs("/content/refdata", exist_ok=True)

def dl(url, path):
    print(f"[DL] {url}")
    r = requests.get(url, timeout=30)
    r.raise_for_status()
    with open(path, "wb") as f:
        f.write(r.content)
    sha = hashlib.sha256(r.content).hexdigest()
    print(f"[OK] Saved: {path}\nSHA256: {sha}\n")
    return path


# ================================================================
# 1) AIRPORT DATA
# ================================================================
print("\n=== AIRPORT DATA ===")

openflights_url = "https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat"
openflights_path = "/content/refdata/airports_openflights.dat"
dl(openflights_url, openflights_path)

airport_code_url = "https://raw.githubusercontent.com/datasets/airport-codes/master/data/airport-codes.csv"
airport_code_path = "/content/refdata/airport_codes.csv"
dl(airport_code_url, airport_code_path)

print("Rows airports_openflights:", sum(1 for _ in open(openflights_path)))
print("Rows airport_codes:", len(pd.read_csv(airport_code_path)))

# ================================================================
# 3) FINAL REPORT
# ================================================================
print("\nALL DONE — ALL FILES SUCCESSFULLY DOWNLOADED & VERIFIED.")
print("Stored under /content/refdata:")
for f in os.listdir("/content/refdata"):
    print(" •", f)



=== AIRPORT DATA ===
[DL] https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat
[OK] Saved: /content/refdata/airports_openflights.dat
SHA256: 9387cdb38df5bd664da823f8ccb69fdd9b33a1888f5b7cca09c34a3cd9ff59f9

[DL] https://raw.githubusercontent.com/datasets/airport-codes/master/data/airport-codes.csv
[OK] Saved: /content/refdata/airport_codes.csv
SHA256: a916fd8b262c9ab87be40229d93bc6ee9756f2a99dcc2b05b8b7a014f7cdeed6

Rows airports_openflights: 7698
Rows airport_codes: 82808

ALL DONE — ALL FILES SUCCESSFULLY DOWNLOADED & VERIFIED.
Stored under /content/refdata:
 • airports_openflights.dat
 • airport_codes.csv


In [5]:
# ================================================================
# MOON METRICS — SKYFIELD (NASA JPL DE421)
# ================================================================
from skyfield.api import load, wgs84
import math
import pandas as pd

ts   = load.timescale()
eph  = load("de421.bsp")   # downloaded automatically
moon = eph["moon"]
sun  = eph["sun"]

def moon_metrics(lat, lon, dt):
    """
    Returns:
      - moon_illumination (0–100%)
      - altitude (deg)
      - azimuth (deg)
      - distance (km)
      - phase_age_days (0–29.53)
    """
    if pd.isna(lat) or pd.isna(lon) or dt is None:
        return {
            "moon_illumination": None,
            "moon_altitude_deg": None,
            "moon_azimuth_deg": None,
            "moon_distance_km": None,
            "moon_phase_age_days": None
        }

    try:
        t = ts.from_datetime(dt)
        observer = wgs84.latlon(lat, lon)

        astrometric = observer.at(t).observe(moon)
        alt, az, distance = astrometric.apparent().altaz()

        # Sun vector for illumination
        sun_app = observer.at(t).observe(sun).apparent()

        phase_angle = sun_app.separation_from(astrometric.apparent()).degrees
        illumination = (1 + math.cos(math.radians(phase_angle))) / 2

        phase_age_days = (phase_angle / 360.0) * 29.530588

        return {
            "moon_illumination": float(illumination * 100.0),
            "moon_altitude_deg": float(alt.degrees),
            "moon_azimuth_deg": float(az.degrees),
            "moon_distance_km": float(distance.km),
            "moon_phase_age_days": float(phase_age_days)
        }

    except:
        return {
            "moon_illumination": None,
            "moon_altitude_deg": None,
            "moon_azimuth_deg": None,
            "moon_distance_km": None,
            "moon_phase_age_days": None
        }


[#################################] 100% de421.bsp


In [6]:
# ================================================================
# GEOMAGNETIC LATITUDE + HAVERSINE DISTANCE (DROP-IN MODULE)
# ================================================================
import math

# ----------------------------------------------------------------
# CONSTANTS (2020 IGRF dipole pole — scientific & transparent)
# ----------------------------------------------------------------
GEOMAG_POLE_LAT = math.radians(80.65)     # degrees → radians
GEOMAG_POLE_LON = math.radians(-72.68)    # degrees → radians
EARTH_RADIUS_KM = 6371.0088               # WGS84 mean radius


# ----------------------------------------------------------------
# FUNCTION: Compute geomagnetic latitude (degrees)
# ----------------------------------------------------------------
def geomagnetic_latitude_deg(lat_deg: float, lon_deg: float) -> float:
    """
    Compute geomagnetic latitude using the IGRF dipole pole projection.
    Scientifically accurate and requires no external data.
    """
    lat = math.radians(lat_deg)
    lon = math.radians(lon_deg)

    term = (
        math.sin(lat) * math.sin(GEOMAG_POLE_LAT)
        + math.cos(lat) * math.cos(GEOMAG_POLE_LAT) * math.cos(lon - GEOMAG_POLE_LON)
    )

    # result in radians
    geomag_lat = math.asin(term)

    return math.degrees(geomag_lat)


# ----------------------------------------------------------------
# FUNCTION: Haversine distance (km)
# ----------------------------------------------------------------
def haversine_km(lat1: float, lon1: float, lat2: float, lon2: float) -> float:
    """
    Great-circle distance using the haversine formula.
    """
    # convert to radians
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = (
        math.sin(dlat / 2)**2 +
        math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2)**2
    )
    c = 2 * math.asin(math.sqrt(a))

    return EARTH_RADIUS_KM * c


# ----------------------------------------------------------------
# OPTIONAL INLINE TESTS
# ----------------------------------------------------------------
if __name__ == "__main__":
    # Example: Roswell, NM
    print("Geomagnetic latitude:", geomagnetic_latitude_deg(33.3943, -104.5230))
    # Example distance: NYC ↔ LA
    print("NY ↔ LA (km):", haversine_km(40.7128, -74.0060, 34.0522, -118.2437))


Geomagnetic latitude: 41.17134641179337
NY ↔ LA (km): 3935.751690893986


In [4]:
!pip install skyfield numpy


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 367.0/367.0 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.7/235.7 kB 16.4 MB/s eta 0:00:00


In [9]:
# ================================================================
# UFO ENRICHMENT PIPELINE — BallTree + Safe Moon (Local-Time → UTC)
# Scientific-grade enrichment:
#   • macro context (600+ fields)
#   • moon metrics (Skyfield, NASA DE421) — local time → UTC
#   • geomagnetic latitude
#   • great-circle distance (Haversine via BallTree)
#   • nearest airport (BallTree, 1945+ cutoff)
#
# Design choices:
#   - Only use existing fields: latitude, longitude, date_time.
#   - No synthetic times or guessed years.
#   - Moon metrics are added ONLY when:
#       * latitude/longitude are valid real coordinates (not NaN, not 0/0)
#       * date_time parses cleanly
#       * we can find a real timezone for that location.
#   - On failure, we log and leave moon_* as None.
# ================================================================

import json
import math
import pandas as pd
from datetime import datetime, timezone
import numpy as np
from sklearn.neighbors import BallTree
from dateutil import parser
from timezonefinder import TimezoneFinder
import pytz

# ================================================================
# INPUT FILES
# ================================================================
UFO_PATH   = "/content/ufo_deduped_v2.jsonl"
MACRO_PATH = "/content/macro_yearly_context_clean_named.parquet"
OUT_PATH   = "/content/ufo_enriched_v2.jsonl"

tf = TimezoneFinder()

# ================================================================
# GEOMAGNETIC LATITUDE + HAVERSINE
# ================================================================
EARTH_RADIUS_KM = 6371.0088

GEOMAG_POLE_LAT = math.radians(80.65)
GEOMAG_POLE_LON = math.radians(-72.68)


def geomagnetic_latitude_deg(lat, lon):
    """Compute geomagnetic latitude (IGRF-style approximation)."""
    lat_r = math.radians(lat)
    lon_r = math.radians(lon)
    term = (
        math.sin(lat_r) * math.sin(GEOMAG_POLE_LAT)
        + math.cos(lat_r) * math.cos(GEOMAG_POLE_LAT) * math.cos(lon_r - GEOMAG_POLE_LON)
    )
    return math.degrees(math.asin(term))


def is_valid_coord(lat, lon):
    """Strict coordinate validity check: numeric, not NaN, not (0,0) sentinel."""
    if not isinstance(lat, (int, float)) or not isinstance(lon, (int, float)):
        return False
    # math.isnan works for floats; ints will be auto-cast
    if math.isnan(lat) or math.isnan(lon):
        return False
    # Treat (0,0) as "no data" sentinel
    if lat == 0.0 and lon == 0.0:
        return False
    return True


# ================================================================
# MOON METRICS — SKYFIELD (NASA DE421)
# ================================================================
from skyfield.api import load, wgs84

ts = load.timescale()
eph = load("de421.bsp")
earth, moon, sun = eph["earth"], eph["moon"], eph["sun"]


def safe_parse_dt_utc(dt_raw, lat, lon):
    """
    Parse a date_time string into a UTC datetime, using only:
      - the given string
      - the given coordinates (for timezone lookup)

    Rules:
      - Reject 'nan', 'none', '', etc. → returns None.
      - If parsing fails → returns None.
      - If parsed datetime has tzinfo → convert to UTC.
      - If no tzinfo:
          * require valid coords
          * use TimezoneFinder(lat, lon) to get a real tz name
          * localize and convert to UTC
          * if timezone unavailable/ambiguous → returns None.
    """
    if not isinstance(dt_raw, str):
        return None

    s = dt_raw.strip()
    if not s:
        return None
    low = s.lower()
    if low in ("nan", "none", "null"):
        return None

    # 1) parse clock time
    try:
        dt_local = parser.parse(s)
    except (ValueError, OverflowError):
        return None

    # 2) If it already has a timezone, just convert to UTC
    if dt_local.tzinfo is not None:
        try:
            return dt_local.astimezone(pytz.utc)
        except Exception:
            return None

    # 3) No tzinfo: we require valid coordinates + real timezone
    if not is_valid_coord(lat, lon):
        return None

    try:
        tzname = tf.timezone_at(lat=lat, lng=lon)
    except Exception:
        tzname = None

    if tzname is None:
        return None

    try:
        local_tz = pytz.timezone(tzname)
    except Exception:
        return None

    try:
        local_dt = local_tz.localize(dt_local, is_dst=None)
    except (pytz.AmbiguousTimeError, pytz.NonExistentTimeError):
        # Ambiguous or nonexistent local times (DST edge cases) → we don't guess.
        return None
    except Exception:
        return None

    try:
        return local_dt.astimezone(pytz.utc)
    except Exception:
        return None


def compute_moon(lat, lon, dt_utc):
    """
    Compute moon metrics given:
      - lat, lon (degrees)
      - dt_utc (datetime in UTC or naive-UTC)

    Uses ts.utc(...) for maximum clarity.
    Only catches ValueError (logs and returns None-fields).
    Other exceptions will surface so they aren't silently swallowed.
    """
    if dt_utc is None:
        return {
            "moon_altitude_deg": None,
            "moon_azimuth_deg": None,
            "moon_distance_km": None,
            "moon_illumination": None,
            "moon_phase_age_days": None,
        }

    # Normalize to naive UTC
    if dt_utc.tzinfo is not None:
        dt_utc = dt_utc.astimezone(timezone.utc).replace(tzinfo=None)

    sec = dt_utc.second + dt_utc.microsecond / 1e6

    try:
        t = ts.utc(dt_utc.year, dt_utc.month, dt_utc.day,
                   dt_utc.hour, dt_utc.minute, sec)

        # Topocentric observer: earth + WGS84 lat/lon
        observer = (earth + wgs84.latlon(lat, lon)).at(t)

        # Moon position
        astrometric = observer.observe(moon)
        alt, az, distance = astrometric.apparent().altaz()

        # Phase angle from sun→moon
        phase_angle = observer.observe(moon).phase_angle(sun).degrees

        # Approximate illuminated fraction (%) from phase angle
        illum_frac = max(
            0.0,
            min(100.0, 100.0 * (1.0 + math.cos(math.radians(phase_angle))) / 2.0),
        )

        # Simple phase-age proxy (not exact physical age, but monotonic)
        age_days = 29.530588 * (phase_angle / 180.0)

        return {
            "moon_altitude_deg": alt.degrees,
            "moon_azimuth_deg": az.degrees,
            "moon_distance_km": distance.km,
            "moon_illumination": illum_frac,
            "moon_phase_age_days": age_days,
        }

    except ValueError as e:
        # Narrow, expected failures (e.g., out-of-range date) → log and return None
        print(f"[compute_moon] ValueError at lat={lat}, lon={lon}, dt_utc={dt_utc}: {e}")
        return {
            "moon_altitude_deg": None,
            "moon_azimuth_deg": None,
            "moon_distance_km": None,
            "moon_illumination": None,
            "moon_phase_age_days": None,
        }


# ================================================================
# AIRPORTS — LOAD + BallTree BUILD
# ================================================================
openflights_path = "/content/refdata/airports_openflights.dat"
airport_codes_path = "/content/refdata/airport_codes.csv"

# ---------- OpenFlights ----------
of = pd.read_csv(openflights_path, header=None)
of = of[[6, 7, 4, 5]]
of.columns = ["lat", "lon", "iata", "icao"]
of["code"] = of["iata"]
of = of.dropna(subset=["lat", "lon"])

# ---------- Airport Codes ----------
ac = pd.read_csv(airport_codes_path)


def parse_coords(s):
    try:
        lon, lat = s.split(",")
        return float(lat), float(lon)
    except Exception:
        return None, None


ac["lat"], ac["lon"] = zip(*ac["coordinates"].apply(parse_coords))
ac["code"] = ac["iata_code"]
ac = ac.dropna(subset=["lat", "lon"])

# ---------- COMBINE ----------
airport_df = pd.concat(
    [
        ac[["code", "lat", "lon"]],
        of[["code", "lat", "lon"]],
    ],
    ignore_index=True,
).dropna(subset=["lat", "lon"]).reset_index(drop=True)

# ---------- BUILD BallTree ----------
airport_points = np.radians(airport_df[["lat", "lon"]].to_numpy())
airport_tree = BallTree(airport_points, metric="haversine")

MIN_AIRPORT_YEAR = 1945

# ================================================================
# LOAD MACRO CONTEXT
# ================================================================
print("=== Loading macro context parquet (600+ fields) ===")
macro = pd.read_parquet(MACRO_PATH).set_index("year")

# ================================================================
# STREAMING ENRICHMENT
# ================================================================
print("\n=== Streaming enrichment start ===")
written = 0

with open(OUT_PATH, "w", encoding="utf-8") as fout:
    with open(UFO_PATH, "r", encoding="utf-8") as fin:
        for line_idx, line in enumerate(fin):
            row = json.loads(line)

            # Pass through metadata header unchanged if present
            if line_idx == 0 and "dataset" in row and "merge_version" in row:
                fout.write(json.dumps(row, ensure_ascii=False) + "\n")
                written += 1
                continue

            # YEAR + macro context (uses existing 'year' field only)
            yr = row.get("year")
            if isinstance(yr, float):
                yr = int(yr)
            if isinstance(yr, int) and yr in macro.index:
                row.update(macro.loc[yr].to_dict())

            # Coordinates + time
            lat = row.get("latitude") or row.get("city_latitude")
            lon = row.get("longitude") or row.get("city_longitude")
            dt_raw = row.get("date_time")

            has_coords = is_valid_coord(lat, lon)

            # ---------- Moon metrics ----------
            if has_coords:
                dt_utc = safe_parse_dt_utc(dt_raw, lat, lon)
                if dt_utc is not None:
                    moon_dict = compute_moon(lat, lon, dt_utc)
                else:
                    moon_dict = {
                        "moon_altitude_deg": None,
                        "moon_azimuth_deg": None,
                        "moon_distance_km": None,
                        "moon_illumination": None,
                        "moon_phase_age_days": None,
                    }
            else:
                moon_dict = {
                    "moon_altitude_deg": None,
                    "moon_azimuth_deg": None,
                    "moon_distance_km": None,
                    "moon_illumination": None,
                    "moon_phase_age_days": None,
                }

            row.update(moon_dict)

            # ---------- Geomagnetic latitude ----------
            if has_coords:
                row["geomagnetic_latitude"] = geomagnetic_latitude_deg(lat, lon)
            else:
                row["geomagnetic_latitude"] = None

            # ---------- Nearest airport ----------
            if has_coords and isinstance(yr, int) and yr >= MIN_AIRPORT_YEAR:
                pt = np.radians([[lat, lon]])
                dist_rad, idx = airport_tree.query(pt, k=1)
                idx = idx[0][0]
                dist_km = dist_rad[0][0] * EARTH_RADIUS_KM

                row["nearest_airport_code"] = airport_df.iloc[idx].code
                row["nearest_airport_km"] = float(dist_km)
                row["nearest_airport_source"] = "openflights+airportcodes_BallTree_1945cut"
            else:
                row["nearest_airport_code"] = None
                row["nearest_airport_km"] = None
                row["nearest_airport_source"] = None

            fout.write(json.dumps(row, ensure_ascii=False) + "\n")
            written += 1

print("=== DONE ===")
print("Wrote:", written)
print("Output:", OUT_PATH)


=== Loading macro context parquet (600+ fields) ===

=== Streaming enrichment start ===
=== DONE ===
Wrote: 242843
Output: /content/ufo_enriched_v2.jsonl


In [8]:
!pip install timezonefinder

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 28.2/28.2 MB 70.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 49.9 MB/s eta 0:00:00


In [ ]:
!tail /content/ufo_enriched_v2.jsonl


{"city": "zutphen (netherlands)", "state": "nan", "date_time": "nan", "shape": "nan", "duration_bucket": -1, "text_hash": "a3d2de7675556553a5f08e4c88d2c228", "raw_snapshot": ["4/18/2010 23:00|zutphen (netherlands)|nan|nan|sphere|120|2 minutes|We saw an orange glowing light in the sky when airspace was closed|4/18/2012|52.142736|6.196058|37622|ufo_sighting_data.csv"], "raw_hash": ["11b66f14ae1958e977a1a9e76802f2ed07b49a42"], "summary": "nan", "full_text": "nan", "duration_seconds": null, "latitude": 52.142736, "longitude": 6.196058, "country": "nan", "year": -1, "year_context_available": false, "ufo_uuid": "9442a05a246962b71a7dcaa1e28fb580", "lineage": [{"file": "ufo_sighting_data.csv", "row": 37622, "raw_hash": "11b66f14ae1958e977a1a9e76802f2ed07b49a42"}], "merge_version": "ufo_v2_2025_01_28", "dedupe_method": "vectorized_signature_v2", "moon_altitude_deg": null, "moon_azimuth_deg": null, "moon_distance_km": null, "moon_illumination": null, "moon_phase_age_days": null, "geomagnetic_lat

In [ ]:
import shutil

shutil.make_archive(
    "/content/ufo_enriched_v2",   # output name (no .zip here)
    "zip",
    "/content",                   # root folder
    "ufo_enriched_v2.jsonl"       # file to include
)


'/content/ufo_enriched_v2.zip'

In [ ]:
import json

path = "/content/ufo_enriched_v2.jsonl"

# read first 5 rows
with open(path, "r", encoding="utf-8") as f:
    for i in range(5):
        row = json.loads(next(f))
        print(row.keys())
        print("-------")


dict_keys(['dataset', 'merge_version', 'generated_at', 'sources', 'dedupe_method', 'uuid_method', 'provenance_fields', 'nearest_airport_code', 'nearest_airport_km', 'nearest_airport_source'])
-------
dict_keys(['city', 'state', 'date_time', 'shape', 'duration_bucket', 'text_hash', 'raw_snapshot', 'raw_hash', 'summary', 'full_text', 'duration_seconds', 'latitude', 'longitude', 'country', 'year', 'year_context_available', 'ufo_uuid', 'lineage', 'merge_version', 'dedupe_method', 'nchs_nchs_top_five_leading_causes_of_death_united_states_1990_1950_2000_number_of_deaths', 'nchs_nchs_age_adjusted_death_rates_for_selected_major_causes_of_death_age_adjusted_death_rate', 'nchs_nchs_death_rates_and_life_expectancy_at_birth_average_life_expectancy_years', 'nchs_nchs_death_rates_and_life_expectancy_at_birth_age_adjusted_death_rate', 'nchs_nchs_leading_causes_of_death_united_states_deaths', 'nchs_nchs_leading_causes_of_death_united_states_age_adjusted_death_rate', 'nchs_nchs_potentially_excess_death

In [10]:
# ================================================================
# UFO ENRICHMENT VALIDATION REPORT
# Validates:
#   • macro context merge
#   • moon metrics
#   • geomagnetic latitude
#   • nearest airport
#   • NO contamination of original fields
# ================================================================

import json
import random
import pandas as pd

ENRICHED_PATH = "/content/ufo_enriched_v2.jsonl"

print("=== VALIDATION REPORT ===")
print("Loading enriched dataset…")

total = 0
has_coords = 0
has_datetime = 0
has_both = 0
has_macro = 0
has_airport = 0
has_moon = 0
has_geomag = 0

sample_rows = []
macro_prefixes = [
    "news_", "gdp_", "arxiv_", "energy_", "market_",
    "ucdp_", "gdelt_", "global_temp_", "disaster_",
    "famous_", "patent_", "nchs_", "air_"
]

with open(ENRICHED_PATH, "r", encoding="utf-8") as f:
    for line in f:
        row = json.loads(line)
        total += 1

        if len(sample_rows) < 20:
            sample_rows.append(row)

        # coordinates
        lat = row.get("latitude") or row.get("city_latitude")
        lon = row.get("longitude") or row.get("city_longitude")
        coords_ok = isinstance(lat, (int,float)) and isinstance(lon, (int,float))
        if coords_ok:
            has_coords += 1

        # datetime (accept anything non-empty string)
        dt = row.get("date_time")
        date_ok = isinstance(dt, str) and len(dt.strip()) > 0
        if date_ok:
            has_datetime += 1
        if coords_ok and date_ok:
            has_both += 1

        # macro context — any field that starts with any macro prefix
        if any(k.startswith(p) for k in row.keys() for p in macro_prefixes):
            has_macro += 1

        # moon metrics — FIXED: now accepts if altitude exists OR illumination exists
        if (
            ("moon_altitude_deg" in row and row["moon_altitude_deg"] is not None)
            or ("moon_illumination" in row and row["moon_illumination"] is not None)
        ):
            has_moon += 1

        # geomagnetic lat
        if "geomagnetic_latitude" in row and row["geomagnetic_latitude"] is not None:
            has_geomag += 1

        # nearest airport
        if row.get("nearest_airport_code") not in (None, ""):
            has_airport += 1

print("\n=== COVERAGE SUMMARY ===")
print(f"Total rows:                        {total:,}")
print(f"Rows w/ valid coordinates:         {has_coords:,}")
print(f"Rows w/ valid datetime:            {has_datetime:,}")
print(f"Rows w/ BOTH coords + datetime:    {has_both:,}")
print()
print(f"Rows w/ macro context:             {has_macro:,}")
print(f"Rows w/ moon metrics:              {has_moon:,}")
print(f"Rows w/ geomagnetic latitude:      {has_geomag:,}")
print(f"Rows w/ nearest airport:           {has_airport:,}")

def pct(x):
    return f"{(x/total*100):.2f}%"

print("\n=== PERCENTAGES ===")
print(f"Macro context coverage:            {pct(has_macro)}")
print(f"Moon metric coverage:              {pct(has_moon)}")
print(f"Geomagnetic lat coverage:          {pct(has_geomag)}")
print(f"Nearest airport coverage:          {pct(has_airport)}")

print("\n=== CHECK FOR FIELD CONTAMINATION ===")

ORIGINAL_FIELDS = {
    "city","state","date_time","shape","duration_bucket","text_hash",
    "raw_snapshot","raw_hash","summary","full_text","duration_seconds",
    "latitude","longitude","country","year","year_context_available",
    "ufo_uuid","lineage","merge_version","dedupe_method"
}

added_fields = []
for k in sample_rows[0].keys():
    if k not in ORIGINAL_FIELDS:
        added_fields.append(k)

print("Fields added by enrichment:", len(added_fields))
print(sorted(added_fields)[:50], "… (truncated)")

print("\n=== RANDOM SAMPLE CHECK (5 rows) ===")
for r in random.sample(sample_rows, 5):
    print("-"*50)
    print("city:", r.get("city"))
    print("date_time:", r.get("date_time"))
    print("latitude/longitude:", r.get("latitude"), r.get("longitude"))
    print("moon_altitude_deg:", r.get("moon_altitude_deg"))
    print("geomagnetic_latitude:", r.get("geomagnetic_latitude"))
    print("nearest_airport_code:", r.get("nearest_airport_code"))
    print("macro example gdp_gdp_growth_mean:", r.get("gdp_gdp_growth_mean"))


=== VALIDATION REPORT ===
Loading enriched dataset…

=== COVERAGE SUMMARY ===
Total rows:                        242,843
Rows w/ valid coordinates:         106,374
Rows w/ valid datetime:            242,842
Rows w/ BOTH coords + datetime:    106,374

Rows w/ macro context:             86,750
Rows w/ moon metrics:              85,299
Rows w/ geomagnetic latitude:      106,374
Rows w/ nearest airport:           85,273

=== PERCENTAGES ===
Macro context coverage:            35.72%
Moon metric coverage:              35.13%
Geomagnetic lat coverage:          43.80%
Nearest airport coverage:          35.11%

=== CHECK FOR FIELD CONTAMINATION ===
Fields added by enrichment: 5
['dataset', 'generated_at', 'provenance_fields', 'sources', 'uuid_method'] … (truncated)

=== RANDOM SAMPLE CHECK (5 rows) ===
--------------------------------------------------
city: &ccedil;anakkale (turkey)
date_time: 11/16/2002 06:55
latitude/longitude: 40.155312 26.41416
moon_altitude_deg: -28.91432093156959
geomagn

In [ ]:
!pip install timezonefinder


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 28.2/28.2 MB 25.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 27.5 MB/s eta 0:00:00


In [11]:
import os
import zipfile

input_path = "/content/ufo_enriched_v2.jsonl"
zip_path   = "/content/ufo_enriched_v2.zip"

# Create ZIP
with zipfile.ZipFile(zip_path, "w", compression=zipfile.ZIP_DEFLATED) as zf:
    # arcname makes the file inside the zip just "ufo_enriched_v2.jsonl"
    zf.write(input_path, arcname=os.path.basename(input_path))

print("Wrote:", zip_path)

# If you're in Colab and want to download to your machine:
try:
    from google.colab import files
    files.download(zip_path)
except ImportError:
    print("Not in Colab, just use the zip path directly.")


Wrote: /content/ufo_enriched_v2.zip


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>